In [1]:
# Enable autoreload extension to automatically reload modules
%load_ext autoreload
%autoreload 1

# Import necessary modules and libraries
#from AirSeaFluxCode import AirSeaFluxCode  # Import AirSeaFluxCode class from AirSeaFluxCode module
import xarray as xr  # Import xarray library with alias xr
import gsw_xarray as gsw  # Import gsw_xarray module with alias gsw
import matplotlib.dates as mdates  # Import module for working with dates in matplotlib
import matplotlib.pyplot as plt  # Import matplotlib.pyplot for plotting
import numpy as np  # Import numpy library with alias np for numerical operations
import cartopy.crs as ccrs  # Import cartopy for geospatial data visualization
import cmocean.cm as cmo  # Import colormaps from cmocean for oceanography
from matplotlib.lines import Line2D
import statsmodels.api as sm
from matplotlib.ticker import FuncFormatter
from collections import defaultdict
from tqdm.notebook import tqdm_notebook as tqdm
import scipy.stats as sstats
import pandas as pd
from joblib import Parallel, delayed
import matplotlib.patches as patches
from matplotlib.ticker import MaxNLocator
from matplotlib.colors import LogNorm
from matplotlib.patches import ConnectionPatch
import seaborn as sns
import scipy
import string

# Import my_funcs module for interactive reloading
%aimport my_funcs

# Call update_params function from my_funcs module to update parameters
my_funcs.update_params(fontsize=24)


# Define color variables with hexadecimal color codes
c20 = "#C13F89"  # Define color c20
#c22 = "#3ec177"  # Define color c22
#c23 = "#3e88c1"  # Define color c23
c22 = "#00B4D8"  # Define color c22
c23 = "#0077B6"  # Define color c23
ext = "#a43ec1"  # Define color ext

# Manually create Line2D objects for legend handles
legend_lines = [
    Line2D([], [], color=c20, lw=3, label='SD1020'),
    Line2D([], [], color=c22, lw=3, label='SD1022'),
    Line2D([], [], color=c23, lw=3, label='SD1023')]

# Manually create Line2D objects for legend handles
legend_dots = [
    Line2D([], [], color=c20, lw=0, marker='.', ms=25, label='SD1020'),
    Line2D([], [], color=c22, lw=0, marker='.', ms=25, label='SD1022'),
    Line2D([], [], color=c23, lw=0, marker='.', ms=25, label='SD1023')]


#f'{x*100:.0f}%'
colors = [c20, c22, c23]
labels = ["SD1020", "SD1022", "SD1023"]

def white_or_black(color):
    
    c1 = "white" if color == "white" else "black"
    c2 = "black" if color == "white" else "white"
    
    plt.rcParams.update({
        'figure.facecolor': c1,  # Background color of the figure
        'axes.facecolor': c1,    # Background color inside the plot area
        'savefig.facecolor': c1, # Background color when saving the figure
        'axes.edgecolor': c2,    # Color of the axes border
        'axes.labelcolor': c2,   # Color of the axis labels
        'xtick.color': c2,       # Color of the x-tick labels
        'ytick.color': c2,       # Color of the y-tick labels
        'text.color': c2,        # Default text color
        'axes.titlecolor': c2,   # Color of the plot title
        'font.size': 24,              # Size of the font
    })

### Load and process datasets

In [2]:
ds20 = xr.open_dataset("../data/ds20qc_1min_height.nc")
ds22 = xr.open_dataset("../data/ds22qc_1min_height.nc")
ds23 = xr.open_dataset("../data/ds23qc_1min_height.nc")

In [3]:
def bin_distance(ds):
    ds["dist"] = (ds["distance"]*5).round(0)/5
    dsd = ds.swap_dims({"time":"dist"}).groupby("dist").median("dist")
    return dsd

In [ ]:
ds20d = bin_distance(ds20)
ds22d = bin_distance(ds22)
ds23d = bin_distance(ds23)

In [57]:
ds20d.to_netcdf("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/ds20d.nc")
ds22d.to_netcdf("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/ds22d.nc")
ds23d.to_netcdf("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/ds23d.nc")

In [56]:
# Process and save datasets
var_to_save = ["dist","latitude","wind_speed","TEMP_AIR_MEAN","TEMP_CTD_RBR_MEAN","RH_MEAN","sensible"]
my_funcs.process_and_save(ds20d, var_to_save, '/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_200m_subset20.csv')
my_funcs.process_and_save(ds22d, var_to_save, '/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_200m_subset22.csv')
my_funcs.process_and_save(ds23d, var_to_save, '/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_200m_subset23.csv')


Running through each distance bin:   0%|          | 0/500 [00:00<?, ?it/s]

Running through each distance bin:   0%|          | 0/500 [00:00<?, ?it/s]

Running through each distance bin:   0%|          | 0/500 [00:00<?, ?it/s]

In [5]:
var_to_save = ["time","latitude","wind_speed","TEMP_AIR_MEAN","TEMP_CTD_RBR_MEAN","RH_MEAN","sensible"]
my_funcs.process_and_save_time(ds20, var_to_save, '/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_time_subset20.csv')
my_funcs.process_and_save_time(ds22, var_to_save, '/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_time_subset22.csv')
my_funcs.process_and_save_time(ds23, var_to_save, '/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_time_subset23.csv')


Running through each distance bin:   0%|          | 0/1440 [00:00<?, ?it/s]


KeyboardInterrupt



In [ ]:
fig,axs = plt.subplots(1,4,figsize=(16,4), constrained_layout=True)

bxs=[]

for ax in axs:
    bxs.append(ax.twiny())

for ax,bx,variable,name,unit,ylim in zip(axs,bxs,variables,names,units,ylims):
    
    ds20d[variable].plot(ax=ax)
    ds20[variable].plot(ax=bx,c="C1")
    
    ax.text(0.01,0.01,f"Space mean: {np.nanmean(ds20d[variable]).round(1)}",c="C0",transform=ax.transAxes)
    ax.text(0.01,0.07,f"Time mean: {np.nanmean(ds20[variable]).round(1)}",c="C1",transform=ax.transAxes)

    ax.set(ylabel=f"{name} ({unit})",xlabel="Distance (km)",ylim=ylim)
    bx.set(xlabel="")
    

In [ ]:
fig,axs = plt.subplots(1,4,figsize=(32,8), constrained_layout=True)

bxs=[]

for ax in axs:
    bxs.append(ax.twiny())

for ax,bx,variable,name,unit,ylim in zip(axs,bxs,variables,names,units,ylims):

    
    ds22d[variable].plot(ax=ax)
    ds22[variable].plot(ax=bx,c="C1")
    
    ax.text(0.01,0.01,f"Space mean: {np.nanmean(ds22d[variable]).round(1)}",c="C0",transform=ax.transAxes)
    ax.text(0.01,0.07,f"Time mean: {np.nanmean(ds22[variable]).round(1)}",c="C1",transform=ax.transAxes)

    ax.set(ylabel=f"{name} ({unit})",xlabel="Distance (km)",ylim=ylim)
    bx.set(xlabel="")
    

In [ ]:
fig,axs = plt.subplots(1,4,figsize=(32,8), constrained_layout=True)

bxs=[]

for ax in axs:
    bxs.append(ax.twiny())

for ax,bx,variable,name,unit,ylim in zip(axs,bxs,variables,names,units,ylims):
    
    ds23d[variable].plot(ax=ax)
    ds23[variable].plot(ax=bx,c="C1")
    
    ax.text(0.01,0.01,f"Space mean: {np.nanmean(ds23d[variable]).round(1)}",c="C0",transform=ax.transAxes)
    ax.text(0.01,0.07,f"Time mean: {np.nanmean(ds23[variable]).round(1)}",c="C1",transform=ax.transAxes)

    ax.set(ylabel=f"{name} ({unit})",xlabel="Distance (km)",ylim=ylim)
    bx.set(xlabel="")
    

In [4]:
ds20d = xr.open_dataset("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/ds20d.nc")
ds22d = xr.open_dataset("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/ds22d.nc")
ds23d = xr.open_dataset("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/ds23d.nc")

In [5]:
ss20 = pd.read_csv("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_200m_subset20.csv")
ss22 = pd.read_csv("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_200m_subset22.csv")
ss23 = pd.read_csv("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_200m_subset23.csv")

ss20["Distance"] = ss20["Distance"]/5
ss22["Distance"] = ss22["Distance"]/5
ss23["Distance"] = ss23["Distance"]/5

In [6]:
stats20 = my_funcs.calc_stats(ss20)
stats22 = my_funcs.calc_stats(ss22)
stats23 = my_funcs.calc_stats(ss23)

In [7]:
tss20 = pd.read_csv("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_time_subset20.csv")
tss22 = pd.read_csv("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_time_subset22.csv")
tss23 = pd.read_csv("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/data/output_time_subset23.csv")

tss20["Hours"] = tss20["Minutes"]/60
tss22["Hours"] = tss22["Minutes"]/60
tss23["Hours"] = tss23["Minutes"]/60

tstats20 = my_funcs.calc_stats_time(tss20)
tstats22 = my_funcs.calc_stats_time(tss22)
tstats23 = my_funcs.calc_stats_time(tss23)

## Plot cones

In [11]:
def plot_cone_plots_time(dists,means,stats,ax,bins,vmin,vmax,cbar,cmap):

    img = my_funcs.plot_cone(dists, means, ax, bins,cmap,vmin,vmax,cbar=False)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p95']-ym).plot(ax=ax,c='w',lw=5,zorder=4)
    (stats.sel(days=slice(0,bins[0][-1]))['p95']).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(days=slice(0,bins[0][-1]))['p75']).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p05']-ym).plot(ax=ax,c='w',lw=5,zorder=4)
    # (stats.sel(days=slice(0,bins[0][-1]))['p25']).plot(ax=ax,c='k',lw=1,zorder=4)
    (stats.sel(days=slice(0,bins[0][-1]))['p05']).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['mean']-ym).plot(ax=ax,c='k',ls="",marker=".",mew=0.2, mec="w",zorder=5,ms=8)
    return img

def plot_cone_plots_dist(dists,means,stats,ax,bins,vmin,vmax,cbar,cmap):

    img = my_funcs.plot_cone(dists, means, ax, bins,cmap,vmin,vmax,cbar=False)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p95']-ym).plot(ax=ax,c='w',lw=5,zorder=4)
    (stats.sel(dist=slice(0,bins[0][-1]))['p95']).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p75']).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p05']-ym).plot(ax=ax,c='w',lw=5,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p25']).plot(ax=ax,c='k',lw=1,zorder=4)
    (stats.sel(dist=slice(0,bins[0][-1]))['p05']).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['mean']-ym).plot(ax=ax,c='k',ls="",marker=".",mew=0.2, mec="w",zorder=5,ms=8)
    return img

In [12]:
tss = ((tss20["Subset_Mean"] - tss20["Subset_Mean"][0]) + (tss22["Subset_Mean"] - tss22["Subset_Mean"][0]) + (tss23["Subset_Mean"] - tss23["Subset_Mean"][0]) )/3
dss = ((ss20["Subset_Mean"] - ss20["Subset_Mean"][0]) + (ss22["Subset_Mean"] - ss22["Subset_Mean"][0]) + (ss23["Subset_Mean"] - ss23["Subset_Mean"][0]) )/3

In [13]:
tstats = ((tstats20 - tstats20["median"][0]) + (tstats22 - tstats22["median"][0]) + (tstats23 - tstats23["median"][0]))/3
dstats = ((stats20 - stats20["median"][0]) + (stats22 - stats22["median"][0]) + (stats23 - stats23["median"][0]))/3

In [14]:
def plot_cone_plots_time(dists,means,stats,ax,bins,vmin,vmax,cbar,cmap):

    img = my_funcs.plot_cone(dists, means, ax, bins,cmap,vmin,vmax,cbar=False)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p95']-ym).plot(ax=ax,c='w',lw=5,zorder=4)
    (stats.sel(days=slice(0,bins[0][-1]))['p95']-stats.sel(days=slice(0,bins[0][-1]))['p95'][0]).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(days=slice(0,bins[0][-1]))['p75']).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p05']-ym).plot(ax=ax,c='w',lw=5,zorder=4)
    # (stats.sel(days=slice(0,bins[0][-1]))['p25']).plot(ax=ax,c='k',lw=1,zorder=4)
    (stats.sel(days=slice(0,bins[0][-1]))['p05']-stats.sel(days=slice(0,bins[0][-1]))['p05'][0]).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['mean']-ym).plot(ax=ax,c='k',ls="",marker=".",mew=0.2, mec="w",zorder=5,ms=8)
    return img

def plot_cone_plots_dist(dists,means,stats,ax,bins,vmin,vmax,cbar,cmap):

    img = my_funcs.plot_cone(dists, means, ax, bins,cmap,vmin,vmax,cbar=False)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p95']-ym).plot(ax=ax,c='w',lw=5,zorder=4)
    (stats.sel(dist=slice(0,bins[0][-1]))['p95']-stats.sel(dist=slice(0,bins[0][-1]))['p95'][0]).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p75']).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p05']-ym).plot(ax=ax,c='w',lw=5,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['p25']).plot(ax=ax,c='k',lw=1,zorder=4)
    (stats.sel(dist=slice(0,bins[0][-1]))['p05']-stats.sel(dist=slice(0,bins[0][-1]))['p05'][0]).plot(ax=ax,c='k',lw=1,zorder=4)
    # (stats.sel(dist=slice(0,bins[0][-1]))['mean']-ym).plot(ax=ax,c='k',ls="",marker=".",mew=0.2, mec="w",zorder=5,ms=8)
    return img

### Plot combined datasets - sample spread, uncertainty, and probability

## Figure 7

In [ ]:
fig,axs = plt.subplots(3,2,figsize=(16,12), sharey="row", sharex="col", constrained_layout=True, dpi=600, height_ratios=[2,1,1])

cmap="PuBu"
tlim = 24
td   = 1/60
tx   = 6
dlim = 100
dd   = 0.2
dx   = 20
ylim = 4
vmin=1
vmax=100
tbins = np.arange(0,tlim+td,td) 
dbins = np.arange(0-0.1,dlim+dd,dd) 
sbins = np.arange(-10.05,10.05,0.1)

for i,(ax,d,ss,stats,bins,lim,b,x,l) in enumerate(zip(axs[0],
                                                      [tss20["Hours"],ss20["Distance"]],
                                                      [tss,dss],
                                                      [tstats,dstats],
                                                      [tbins,dbins],
                                                      [tlim,dlim],
                                                      [td,dd],
                                                      [tx,dx],
                                                      ["(a)","(b)"])):

    if i==0:
        img,hm1 = plot_cone_plots_time(d, ss, stats, ax,[bins,sbins],vmin,vmax,cbar=False,cmap=cmap)
    else:
        img,hm2 = plot_cone_plots_dist(d, ss, stats, ax,[bins,sbins],vmin,vmax,cbar=False,cmap=cmap)

    ax.set(xlabel="", xlim=(0,lim), xticks=np.arange(0,lim+b,x), 
           ylabel=r"Sensible heat flux (W m$^{-2}$)" if  i ==0 else "", ylim=(-ylim,+ylim))
   
cbar=plt.colorbar(img, ax=ax, label='Relative frequency (%)', pad=-0.01, aspect=25, shrink=0.67, extend="max")
cbar.set_ticks([1e0,1e1,1e2])
cbar.set_ticklabels(["1","10","100"])

#######################


treg = scipy.stats.linregress(tstats['days'], -tstats['p05'] + tstats['p95'])
dreg = scipy.stats.linregress(dstats['dist'], -dstats['p05'] + dstats['p95'])

ax = axs[1][0]
bx = axs[1][1]

(-tstats['p05'] + tstats['p95']).plot(ax=ax, c="k", lw=1)
(-dstats['p05'] + dstats['p95']).plot(ax=bx, c="k", lw=1)

tdl = treg.slope * 10 + treg.intercept
ddl = dreg.slope * 50 + dreg.intercept

ax.plot(tstats['days'], treg.slope * tstats['days'] + treg.intercept, c="C0", lw=3)#, label=l + f": {np.round(tstats['days'][tidx].values,1)} hours")
bx.plot(dstats['dist'], dreg.slope * dstats['dist'] + dreg.intercept, c="C0", lw=3)#, label=l + f": {np.round(dstats['dist'][didx].values,1)} km")

ax.axvline(10,lw=1,ls='--',c='0',zorder=3)
ax.axhline(tdl,lw=1,ls='--',c='0',zorder=3)
ax.scatter(10,tdl,c="C1",marker=".",zorder=3,s=100)

bx.axvline(50,lw=1,ls='--',c='0',zorder=3)
bx.axhline(ddl,lw=1,ls='--',c='0',zorder=3)
bx.scatter(50,ddl,c="C1",marker=".",zorder=3,s=100)

ax.set(xlabel="",ylim=(0,6), yticks=np.arange(0,7,2), ylabel="Uncertainty (W m$^{-2}$)")
bx.set(xlabel="",ylim=(0,6), yticks=np.arange(0,7,2))

##############################################################################

for ax,bins,hm,xl,x,dx,yl in zip(axs[2],[tbins[:-1],dbins[:-1]],[hm1[100],hm2[100]],["Sampling scale (hours)","Sampling scale (km)"],[6,20],[1,2],["Probability (%)",""]):

    ax.plot(bins,hm,c="k",lw=1)
    ax.axhline(0,c="k",ls="--",lw=1)
    ax.set(xlabel=xl,ylim=(-10,120),ylabel=yl)
    ax.spines['left'].set_bounds(-10,100)

    axins = ax.inset_axes([0.5, 0.5, 0.5, 0.5],xlim=(0, x), ylim=(0,101))#, xticklabels=[], yticklabels=[])
    axins.plot(bins,hm,c="k")
    ax.indicate_inset_zoom(axins, edgecolor="black")
    axins.spines['top'].set_visible(False)
    axins.set_xticks(np.arange(0,x+dx,dx), minor=True)
    axins.spines['right'].set_visible(False)

##############################################################################


for i,(ax,l) in enumerate(zip(axs.flatten(),string.ascii_lowercase)):
    ax.spines['top'].set_visible(False)
    ax.spines['right'].set_visible(False)
    ax.text(0.02,1,f"({l})",c='k',fontsize="small",transform=ax.transAxes,ha='left',va="top",
            bbox=dict(facecolor='w', edgecolor='None', boxstyle='square',alpha=0.5))       

plt.close()

/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/notebooks/my_funcs.py:530: RuntimeWarning: invalid value encountered in divide
  normalized_heatmap = heatmap / row_sums * 100


## Supplementary figures

### Individual cones

In [ ]:
fig,AX = plt.subplots(3,2, figsize=(16,12), constrained_layout=True, sharex="col", sharey=True, dpi=600)

cmap="PuBu"
vmin=1
vmax=100
labels = ['SD1020','SD1022','SD1023']
colors = [c20,c22,c23]

tx      = tss20["Hours"]
tmeans  = [tss20["Subset_Mean"], tss22["Subset_Mean"], tss23["Subset_Mean"]]
t0means = [tss20["Subset_Mean"][0], tss22["Subset_Mean"][0], tss23["Subset_Mean"][0]]
tstats  = [tstats20, tstats22, tstats23]
txmin   = 0
txmax   = 24
tdx     = 1/60
tbins = np.arange(txmin,txmax+tdx,tdx)

qbins   = np.arange(-10.05,10.05,0.1)

dx      = ss20["Distance"]
dmeans  = [ss20["Subset_Mean"], ss22["Subset_Mean"], ss23["Subset_Mean"]]
d0means = [ss20["Subset_Mean"][0], ss22["Subset_Mean"][0], ss23["Subset_Mean"][0]]
dstats  = [stats20, stats22, stats23]
dxmin   = -0.1
dxmax   = 100
ddx     = 0.2
dbins   = np.arange(dxmin,dxmax+ddx,ddx)

ylabels = ["Sensible heat flux (W m$^{-2}$)",""]
xlabels = ["Sampling scale (hours)","Sampling scale (km)"]
xlims = [(0,24),(0,100)]
xticks = [np.arange(0,24+6,6),np.arange(0,100+20,20)]
yticks = [np.arange(-4,4+2,2),np.arange(-4,4+2,2)]

hms1=[]
hms2=[]
  
for i, (tmean,t0mean, tstat, dmean, 
        d0mean, dstat, label, color) in enumerate(zip(tmeans, t0means, tstats, dmeans, 
                                                      d0means, dstats, labels, colors)):
    for j, (ax, mean, zero_mean, stat, 
            x, bins, xlabel, xlim, xtick, ylabel) in enumerate(zip([AX[i, 0], AX[i, 1]], [tmean, dmean], [t0mean, d0mean],[tstat, dstat], 
                                                                   [tx, dx], [tbins, dbins], xlabels, xlims, xticks, ylabels)):
        
        ym = np.array(mean - zero_mean)

        if j == 0:
            img, hm = plot_cone_plots_time(x, ym, stat, ax, [bins, qbins], vmin, vmax, cbar=False, cmap=cmap)
            hms1.append(hm)

        else:
            img, hm = plot_cone_plots_dist(x, ym, stat, ax, [bins, qbins], vmin, vmax, cbar=False, cmap=cmap)
            hms2.append(hm)

        ax.set(ylabel=ylabel if i == 1 else "", xlabel=xlabel if i == 2 else "", xlim=xlim, xticks=xtick, ylim=(-4, 4))
        ax.text(0.075, 1, f"{label}: {zero_mean.round(1)} W m$^{{-2}}$", c=color, fontsize="small", transform=ax.transAxes, ha='left', va='top')



cbar=plt.colorbar(img, ax=AX.T[1][1], label='Relative frequency (%)', pad=-0.01, aspect=25, shrink=0.67, extend="max")
cbar.set_ticks([1e0,1e1,1e2])
cbar.set_ticklabels(["1","10","100"])

for i,(ax,l) in enumerate(zip(AX.flatten(),string.ascii_lowercase)):
    ax.spines['top'].set_visible(False)
    ax.spines['right'].set_visible(False)
    # if i%2!=0:    
    #     ax.yaxis.set_visible(False)
    #     ax.spines['left'].set_visible(False)
    ax.text(0.02,1,f"({l})",c='k',fontsize="small",transform=ax.transAxes,ha='left',va="top",
            bbox=dict(facecolor='w', edgecolor='None', boxstyle='square',alpha=0.5))       

plt.savefig("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/figures/split_cone_plots.png")
plt.close()

### Individual uncertainties and probabilities

In [ ]:
treg20 = sstats.linregress(tstats20['days'], tstats20['delta'])
treg22 = sstats.linregress(tstats22['days'], tstats22['delta'])
treg23 = sstats.linregress(tstats23['days'], tstats23['delta'])

tregs = [treg20,treg22,treg23]

dreg20 = sstats.linregress(stats20['dist'], stats20['delta'])
dreg22 = sstats.linregress(stats22['dist'], stats22['delta'])
dreg23 = sstats.linregress(stats23['dist'], stats23['delta'])

dregs = [dreg20,dreg22,dreg23]

fig, axs = plt.subplots(2, 2, figsize=(16, 12), constrained_layout=True, sharey="row", sharex="col", dpi=600)

# Plot time series in the top left subplot
for tstats, treg, color, label in zip([tstats20, tstats22, tstats23], tregs, colors, labels):
    ax = axs[0, 0]
    tstats['delta'].plot(ax=ax, c=color, lw=1, alpha=0.5, zorder=1)
    tdl = treg.slope * 10 + treg.intercept
    ax.plot(tstats['days'], treg.slope * tstats['days'] + treg.intercept, zorder=2, c=color, lw=3, label=label + f": {np.round(tdl,1)} W m$^{{-2}}$")
    ax.axhline(tdl, lw=2, ls='--', c=color, zorder=3)
    ax.text(10,0.5," 10 hours",c='k',fontsize="small",va="center",ha="left")
    ax.scatter(10, tdl, zorder=3, fc="k", ec="None", s=100)
    ax.axvline(10, lw=2, ls='--', c='0', zorder=3)
    ax.set(ylabel=r"Uncertainty (W m$^{-2}$)", xlabel='', xlim=(0, 24), xticks=np.arange(0, 24+6, 6), ylim=(0, 6))
    ax.legend(loc='upper left', ncols=1, bbox_to_anchor=[0.005, 0.97],
              frameon=True, framealpha=1, edgecolor='None', handlelength=1, fontsize="small")

# Plot distance series in the top right subplot
for dstats, dreg, color, label in zip([stats20, stats22, stats23], dregs, colors, labels):
    ax = axs[0, 1]
    dstats['delta'].plot(ax=ax, c=color, lw=1, alpha=0.5, zorder=1)
    ddl = dreg.slope * 50 + dreg.intercept
    ax.plot(dstats['dist'], dreg.slope * dstats['dist'] + dreg.intercept, zorder=2, c=color, lw=3, label=label + f": {np.round(ddl,1)} W m$^{{-2}}$")
    ax.axhline(ddl, lw=2, ls='--', c=color, zorder=3)
    ax.text(50,0.5," 50 km",c='k',fontsize="small",va="center",ha="left")
    ax.scatter(50, ddl, zorder=3, fc="k", ec="None", s=100)
    ax.axvline(50, lw=2, ls='--', c='0', zorder=3)
    ax.set(ylabel=r"", xlabel='', xlim=(0, 100), xticks=np.arange(0, 100+20, 20), ylim=(0, 6))
    ax.legend(loc='upper left', ncols=1, bbox_to_anchor=[0.005, 0.97],
              frameon=True, framealpha=1, edgecolor='None', handlelength=1, fontsize="small")

# Plot the probability of mean for time and distance series in the bottom subplots
for ax, hms, bins, xlabel, xlim, xtick, inset_xlim, inset_xtick in zip(
    [axs[1, 0], axs[1, 1]], [hms1, hms2], [tbins[:-1], dbins[:-1]], 
    ['Sampling scale (hours)', 'Sampling scale (km)'], [(0, 24), (0, 100)], 
    [np.arange(0, 24+6, 6), np.arange(0, 100+20, 20)], [(0, 6), (0, 20)], 
    [np.arange(0, 6+1, 1), np.arange(0, 20+2, 2)]):

    axins = ax.inset_axes([0.5, 0.5, 0.5, 0.5], xlim=inset_xlim, ylim=(0, 100))
    ax.spines['left'].set_bounds(0, 100)

    for hm, color in zip(hms, colors):
        ax.plot(bins, hm[100], c=color)
        axins.plot(bins, hm[100], c=color)

    ax.set(ylabel=r"Probability (%)" if ax == axs[1, 0] else "", xlabel=xlabel, xlim=xlim, xticks=xtick, ylim=(0, 110), yticks=np.arange(0, 120, 20))
    
    ax.indicate_inset_zoom(axins, edgecolor="black")
    axins.spines['top'].set_visible(False)
    axins.set_xticks(inset_xtick, minor=True)
    axins.spines['right'].set_visible(False)



for i,(ax,l) in enumerate(zip(axs.flatten(),string.ascii_lowercase)):
    ax.spines['top'].set_visible(False)
    ax.spines['right'].set_visible(False)
    # if i%2!=0:    
    #     ax.yaxis.set_visible(False)
    #     ax.spines['left'].set_visible(False)
    ax.text(0.02,1,f"({l})",c='k',fontsize="small",transform=ax.transAxes,ha='left',va="top",
            bbox=dict(facecolor='w', edgecolor='None', boxstyle='square',alpha=0.5))  

plt.savefig("/Users/xedhjo/Documents/Projects/Southern-Ocean-heat-flux-and-fronts/figures/sample-uncertainty-and-probability.png",dpi=600)
plt.close()

